In [1]:
# Preprocessing & results----------------
from sklearn.model_selection import train_test_split, cross_validate, cross_val_score, GridSearchCV
from sklearn.metrics import classification_report, accuracy_score, f1_score, balanced_accuracy_score
from sklearn.preprocessing import LabelEncoder, StandardScaler

# Models-------------------------
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression, RidgeClassifier, SGDClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.gaussian_process import GaussianProcessClassifier
import sklearn.gaussian_process.kernels as kls
from sklearn.neural_network import MLPClassifier
from sklearn.svm import SVC
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.ensemble import AdaBoostClassifier, RandomForestClassifier, BaggingClassifier, ExtraTreesClassifier

# General purpose
import re
import pandas as pd
import pickle
import numpy as np
from collections import Counter
import warnings
warnings.filterwarnings('ignore')

In [2]:
data_type = 'mind-wandering'

In [3]:
def load_dataset(user_split = True, runidx=1, data_type='mind-wandering'):
    X_train = None
    y_train_medid = None
    y_train_subjid = None
    X_val = None
    y_val_medid = None
    y_val_subjid = None
    X_test = None
    y_test_medid = None
    y_test_subjid = None

    # user_split: Determines the creation of train/val/test set. In user_split, test/val users are never seen during the train. time_split randomly splits each user's chunks into train/val/test.
    if user_split:
        data_file_path = '../../iconip_data/{}/user_based_splits_with_timestamp_RUN{}.pkl'.format(data_type, runidx)
    else:
        data_file_path = '../../iconip_data/{}/time_based_splits_with_timestamp_RUN{}.pkl'.format(data_type, runidx)

    with open(data_file_path, 'rb') as f:
        all_data_splits = pickle.load(f)
        
        X_train = all_data_splits['train']['x']
        y_train_medid = all_data_splits['train']['y_med']
        y_train_subjid = all_data_splits['train']['y_subj']
        y_train_ts = all_data_splits['train']['y_ts']

        X_val = all_data_splits['val']['x']
        y_val_medid = all_data_splits['val']['y_med']
        y_val_subjid = all_data_splits['val']['y_subj']
        y_val_ts = all_data_splits['val']['y_ts']

        X_test = all_data_splits['test']['x']
        y_test_medid = all_data_splits['test']['y_med']
        y_test_subjid = all_data_splits['test']['y_subj']
        y_test_ts = all_data_splits['test']['y_ts']

    return X_train, y_train_medid, y_train_subjid, y_train_ts, X_val, y_val_medid, y_val_subjid, y_val_ts, X_test, y_test_medid, y_test_subjid, y_test_ts

In [4]:
clf_dict = {
    'DecisionTree': {"model": DecisionTreeClassifier(random_state=42), "params": {'max_depth': list(range(2, 64, 10))}},
    'RandomForest': {"model": RandomForestClassifier(random_state=42),
                     "params": {'n_estimators': list(range(5, 100, 20)), 'max_depth': list(range(2, 64, 10))}},
    'LogisticR_L1': {"model": LogisticRegression(random_state=42, max_iter=500),
                     "params": {'penalty': ['l1'], 'solver': ['liblinear', 'saga']}},
    'LogisticR_L2': {"model": LogisticRegression(random_state=42, max_iter=1000),
                     "params": {'penalty': ['l2'], 'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga']}},
    'LogisticR': {"model": LogisticRegression(random_state=42, max_iter=500),
                  "params": {'penalty': ['none'], 'solver': ['newton-cg', 'lbfgs', 'sag', 'saga']}},
    'RidgeClf': {"model": RidgeClassifier(max_iter=1000), "params": {}},
    'SVC_linear': {"model": SVC(random_state=42), "params": {'kernel': ['linear'], 
                                                             'C': [0.5, 1.5, 2.5]}},
    'SVC_poly': {"model": SVC(random_state=42),
                 "params": {'kernel': ['poly'], 'degree': [3, 4, 5], 'gamma': ['scale', 'auto'], 
                            'C': [0.5, 1.5, 2.5]}},
    'SVC_others': {"model": SVC(random_state=42), "params": {'kernel': ['rbf', 'sigmoid'], 
                                                             'gamma': ['scale', 'auto'], 
                                                             'C': [0.5, 1.5, 2.5]}},
    'GussianNB': {"model": GaussianNB(), "params": {}},
    'KNN': {"model": KNeighborsClassifier(), "params": {'n_neighbors': list(range(3, 30))}},
# #     'GaussianProcessClf': {"model": GaussianProcessClassifier(random_state=42, kernel=kls.RBF()), "params": {}},
    'Bagging_SVC': {"model": BaggingClassifier(random_state=42), "params": {'n_estimators': list(range(5, 100, 20)),
                                                                            'base_estimator': [SVC(kernel='linear'),
                                                                                               SVC(kernel='poly',
                                                                                                   degree=3,
                                                                                                   gamma='scale')]}},
    'BaggingDT': {"model": BaggingClassifier(random_state=42), "params": {'n_estimators': list(range(5, 100, 20)),
                                                                          'base_estimator': [
                                                                              DecisionTreeClassifier(random_state=42,
                                                                                                     max_depth=2),
                                                                              DecisionTreeClassifier(random_state=42,
                                                                                                     max_depth=5),
                                                                              DecisionTreeClassifier(random_state=42,
                                                                                                     max_depth=10)]}},
    'AdaBoost': {"model": AdaBoostClassifier(random_state=42), "params": {'n_estimators': list(range(10, 100, 20)),
                                                                          'base_estimator': [DecisionTreeClassifier(
                                                                                                 random_state=42,
                                                                                                 max_depth=2),
                                                                                             DecisionTreeClassifier(
                                                                                                 random_state=42,
                                                                                                 max_depth=12),
                                                                                             DecisionTreeClassifier(
                                                                                                 random_state=42,
                                                                                                 max_depth=12)]}},
    'ExtraTrees': {"model": ExtraTreesClassifier(random_state=42), "params": {'n_estimators': list(range(5, 105, 30)), 
                                                                              'max_depth': [2,5,10,15]}},
    'MLP_l1': {"model": MLPClassifier(random_state=42), "params": {'hidden_layer_sizes': [(x,) for x in 
                                                                                          range(50, 600, 200)], 
                                                                  'activation': ['logistic', 'tanh', 'relu'],
                                                                  'solver': ['adam', 'sgd'], 'early_stopping': 
                                                                   [True]}},
    'MLP_l2': {"model": MLPClassifier(random_state=42), "params": {'hidden_layer_sizes': [(x, y) for x in 
                                                                                          range(50, 600, 200) 
                                                                                          for y in range(50, 360, 200)], 
                                                                  'activation': ['logistic', 'tanh', 'relu'],
                                                                  'solver': ['adam', 'sgd'], 'early_stopping': 
                                                                                               [True]}},
#     'MLP_l3': {"model": MLPClassifier(random_state=42), "params": {'hidden_layer_sizes': [(x, y, z) for x in 
#                                                                                           range(50, 600, 100) 
#                                                                                           for y in range(50, 600, 100)
#                                                                                           for z in range(50, 360, 100)], 
#                                                                   'activation': ['logistic', 'tanh', 'relu'],
#                                                                   'solver': ['adam', 'sgd'], 'early_stopping': 
#                                                                                                [True]}},
}


In [8]:
def predict_med_control_vs_expert(data_type):
    model_results = pd.DataFrame()

    for runidx in range(1, 6):
        model_results['{}_Train_Acc'.format(runidx)] = None
        model_results['{}_Val_Acc'.format(runidx)] = None
        model_results['{}_Test_Acc'.format(runidx)] = None
        model_results['{}_best_params'.format(runidx)] = None

    best_clf_ours = None
    best_clf_val = 0

    for runidx in range(1, 6):
        print("RUN ID: ", runidx)
        user_split   = True
        med_tech_clf = True
        
        X_train, y_train_medid, y_train_subjid, y_train_ts, X_val, y_val_medid, y_val_subjid, y_val_ts, X_test, y_test_medid, y_test_subjid, y_test_ts = load_dataset(user_split=user_split, runidx=runidx, data_type=data_type)
        ## Convert data to binary classification task, i.e. meditation expert vs control group
        y_train_medid = y_train_medid//3
        y_val_medid = y_val_medid//3
        y_test_medid = y_test_medid//3

        # Take data average to reshape to just 64 dim vecs
        X_train_list = []
        X_val_list = []
        X_test_list = []

        for i in range(X_train.shape[0]):
            X_train_list.append(np.mean(X_train[i,:,:], axis=1))
        X_train_list = np.array(X_train_list)
        #print(X_train.shape, X_train_list.shape)

        for i in range(X_val.shape[0]):
            X_val_list.append(np.mean(X_val[i,:,:], axis=1))
        X_val_list = np.array(X_val_list)
        #print(X_val.shape, X_val_list.shape)

        for i in range(X_test.shape[0]):
            X_test_list.append(np.mean(X_test[i,:,:], axis=1))
        X_test_list = np.array(X_test_list)
        #print(X_test.shape, X_test_list.shape)

        # For keeping only 64 channels data
        X_train_df = pd.DataFrame(X_train_list, columns=[str(x) for x in range(0, 64)])
        X_val_df = pd.DataFrame(X_val_list, columns=[str(x) for x in range(0, 64)])
        X_test_df = pd.DataFrame(X_test_list, columns=[str(x) for x in range(0, 64)])

        for clf_name, clf in clf_dict.items():
            classifier = GridSearchCV(clf['model'], clf['params'], n_jobs=20, verbose=0)
            classifier.fit(X_train_df, y_train_medid)
            best_model = classifier.best_estimator_
            
            y_predicted = best_model.predict(X_val_df)
            val_acc = accuracy_score(y_val_medid, y_predicted)
            bal_val_acc = balanced_accuracy_score(y_val_medid, y_predicted)
            
            if bal_val_acc > best_clf_val:
                best_clf_val = bal_val_acc
                best_clf_ours = best_model
                
            y_predicted = best_model.predict(X_test_df)
            test_acc = balanced_accuracy_score(y_test_medid, y_predicted)
            
            print(clf_name, classifier.best_score_, classifier.best_params_, val_acc, bal_val_acc, test_acc)

            model_results.loc[clf_name, ['{}_Train_Acc'.format(runidx), '{}_Val_Acc'.format(runidx), '{}_Test_Acc'.format(runidx), '{}_best_params'.format(runidx)]] = [classifier.best_score_, bal_val_acc, test_acc, classifier.best_params_]
            if user_split:
                model_results.to_csv('./RESULTS_T2{}_MED_BINARYPRED_{}.csv'.format('USER', data_type))
            else:
                model_results.to_csv('./RESULTS_T2_MED_BINARYPRED_{}.csv'.format(data_type))

    return model_results

In [9]:
model_results = predict_med_control_vs_expert(data_type)

RUN ID:  1
DecisionTree 0.9896733276043621 {'max_depth': 12} 0.5884194053208138 0.3906793589919189 0.49789688739334215
RandomForest 0.9990171990171991 {'max_depth': 12, 'n_estimators': 25} 0.7323943661971831 0.4775510204081633 0.4596602972399151


/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fit

LogisticR_L1 0.9985233778337227 {'penalty': 'l1', 'solver': 'liblinear'} 0.4475743348982786 0.29183673469387755 0.43177903296879383
LogisticR_L2 0.9985233778337227 {'penalty': 'l2', 'solver': 'liblinear'} 0.5446009389671361 0.39480208190658816 0.5521371630012418


/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fit

LogisticR 0.9990159886711611 {'penalty': 'none', 'solver': 'newton-cg'} 0.539906103286385 0.3940761539515135 0.6052157192645115
RidgeClf 0.9990147783251231 {} 0.3270735524256651 0.2202711957266128 0.516183952249329
SVC_linear 0.9985245881797606 {'C': 0.5, 'kernel': 'linear'} 0.568075117370892 0.4451376523763868 0.8545447261947683
SVC_poly 0.9990147783251231 {'C': 0.5, 'degree': 3, 'gamma': 'auto', 'kernel': 'poly'} 0.6369327073552425 0.41997671551842214 0.6220406201177743
SVC_others 0.9985245881797606 {'C': 0.5, 'gamma': 'auto', 'kernel': 'rbf'} 0.7652582159624414 0.5176619641145048 0.5198894363658214
GussianNB 0.736977281804868 {} 0.24100156494522693 0.2669017942747569 0.5193286063373793
KNN 1.0 {'n_neighbors': 5} 0.6494522691705791 0.5378989179564443 0.7708208148059128
Bagging_SVC 0.9985245881797606 {'base_estimator': SVC(kernel='linear'), 'n_estimators': 25} 0.568075117370892 0.4451376523763868 0.8597324039578577
BaggingDT 0.9950847847399572 {'base_estimator': DecisionTreeClassifier

...

/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fit

/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fit

/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fit

/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fitted with feature names
  warnings.warn(
/home/singh_shruti/anaconda3/envs/compneuro/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but MLPClassifier was fit

MLP_l2 0.9995133819951338 {'activation': 'relu', 'early_stopping': True, 'hidden_layer_sizes': (450, 250), 'solver': 'adam'} 0.6736334405144695 0.4447983014861996 0.5


In [10]:
model_results

1_Train_Acc 1_Val_Acc 1_Test_Acc  \
DecisionTree    0.989673  0.390679   0.497897   
RandomForest    0.999017  0.477551    0.45966   
LogisticR_L1    0.998523  0.291837   0.431779   
LogisticR_L2    0.998523  0.394802   0.552137   
LogisticR       0.999016  0.394076   0.605216   
RidgeClf        0.999015  0.220271   0.516184   
SVC_linear      0.998525  0.445138   0.854545   
SVC_poly        0.999015  0.419977   0.622041   
SVC_others      0.998525  0.517662   0.519889   
GussianNB       0.736977  0.266902   0.519329   
KNN                  1.0  0.537899   0.770821   
Bagging_SVC     0.998525  0.445138   0.859732   
BaggingDT       0.995085  0.422449    0.43933   
AdaBoost             1.0  0.565977        0.5   
ExtraTrees           1.0  0.470408   0.550314   
MLP_l1          0.997049  0.351178   0.571866   
MLP_l2          0.998525  0.321723    0.49996   

                                                  1_best_params 2_Train_Acc  \
DecisionTree                                  {'max_depth': 12}     0.99064   
RandomForest              {'max_depth': 12, 'n_estimators': 25}    0.999507   
LogisticR_L1           {'penalty': 'l1', 'solver': 'liblinear'}    0.999015   
LogisticR_L2           {'penalty': 'l2', 'solver': 'liblinear'}    0.999507   
LogisticR            {'penalty': 'none', 'solver': 'newton-cg'}    0.999507   
RidgeClf                                                     {}    0.999507   
SVC_linear                       {'C': 0.5, 'kernel': 'linear'}    0.999015   
SVC_poly      {'C': 0.5, 'degree': 3, 'gamma': 'auto', 'kern...    0.999507   
SVC_others         {'C': 0.5, 'gamma': 'auto', 'kernel': 'rbf'}    0.998522   
GussianNB                                                    {}    0.737931   
KNN                                          {'n_neighbors': 5}         1.0   
Bagging_SVC   {'base_estimator': SVC(kernel='linear'), 'n_es...    0.999507   
BaggingDT     {'base_estimator': DecisionTreeClassifier(max_...    0.997537   
AdaBoost      {'base_estimator': DecisionTreeClassifier(max_...         1.0   
ExtraTrees                {'max_depth': 10, 'n_estimators': 35}         1.0   
MLP_l1        {'activation': 'tanh', 'early_stopping': True,...    0.998522   
MLP_l2        {'activation': 'tanh', 'early_stopping': True,...     0.99803   

             2_Val_Acc 2_Test_Acc  \
DecisionTree  0.745845   0.492422   
RandomForest  0.680626   0.463812   
LogisticR_L1    0.4658   0.684871   
LogisticR_L2  0.489555   0.665845   
LogisticR     0.475195    0.67198   
RidgeClf      0.432782   0.442139   
SVC_linear    0.421073   0.476904   
SVC_poly      0.599062   0.661554   
SVC_others    0.710526    0.45092   
GussianNB     0.731932   0.188139   
KNN           0.748984   0.520209   
Bagging_SVC   0.455012   0.538253   
BaggingDT     0.659467   0.524119   
AdaBoost      0.747878   0.390593   
ExtraTrees    0.729755   0.435583   
MLP_l1        0.433476   0.558884   
MLP_l2        0.639291   0.480152   

                                                  2_best_params 3_Train_Acc  \
DecisionTree                                  {'max_depth': 12}    0.996051   
RandomForest               {'max_depth': 12, 'n_estimators': 5}         1.0   
LogisticR_L1                {'penalty': 'l1', 'solver': 'saga'}         1.0   
LogisticR_L2           {'penalty': 'l2', 'solver': 'liblinear'}         1.0   
LogisticR                  {'penalty': 'none', 'solver': 'sag'}         1.0   
RidgeClf                                                     {}    0.999015   
SVC_linear                       {'C': 0.5, 'kernel': 'linear'}         1.0   
SVC_poly      {'C': 1.5, 'degree': 3, 'gamma': 'auto', 'kern...         1.0   
SVC_others         {'C': 0.5, 'gamma': 'auto', 'kernel': 'rbf'}         1.0   
GussianNB                                                    {}    0.794167   
KNN                                          {'n_neighbors': 3}         1.0   
Bagging_SVC   {'base_estimator': SVC(kernel='linear'), 'n_es...         1.0   
BaggingDT    